In [1]:
# Import our dependencies
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler,OneHotEncoder
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LinearRegression
import tensorflow as tf

In [2]:
# Import dependencies
import os
import pandas as pd
import requests
import re
from bs4 import BeautifulSoup
from datetime import datetime

In [3]:
from nba_api.stats.static import teams
from nba_api.stats.endpoints import leaguegamefinder

In [4]:
pd.set_option("display.max_rows", None, "display.max_columns", None)

In [5]:
def createPlayerDF(stat, year):
    # Set url for given year
    url = f'https://www.basketball-reference.com/leagues/NBA_{year}_{stat}.html'
    page = requests.get(url)
    
    # Convert the page html to a soup object
    soup = BeautifulSoup(page.content, 'html.parser')
    
    # Find the sought after table of data
    table = soup.find_all(class_="full_table")

    # Store the headers/column names
    head = soup.find(class_="thead")
    column_names_raw = [head.text for item in head][0]

    # Clean the column_names_raw list
    column_names = column_names_raw.replace("\n",",").split(",")[2:-1]
    
    # Create the dataframe
    players = []

    for i in range(len(table)):
        player_ = []

        for td in table[i].find_all("td"):
            player_.append(td.text)

        players.append(player_)

    df = pd.DataFrame(players, columns=column_names).set_index("Player")

    # Cleaning the player's name from occasional special characters
    df.index = df.index.str.replace('*', "", regex=True)
    
    return df

In [131]:
def createRosters(team):
    roster = []

    # Set url for given team
    url = f"https://www.basketball-reference.com/teams/{team}/{datetime.now().year}.html"
    page = requests.get(url)

    # Convert the page html to a soup object
    soup = BeautifulSoup(page.content, 'html.parser')

    # Find the sought after table of data
    table = soup.find(id="roster")
    player_table = table.find_all(attrs={"data-stat" : "player"})

    # Create a list of all players in the player table
    for p in player_table[1:]:
        roster.append(p.text)

    # Remove "TW" suffix
    for i in range(len(roster)):
        if "\xa0\xa0(TW)" in roster[i]:
            roster[i] = roster[i].replace("\xa0\xa0(TW)", "")

    return roster

In [208]:
def createPlayerAverages(df):
#     # Store the minutes played before dropping column
#     mins = df["MP"].astype(int)

#     # Calculate player's average minutes per game
#     mpg = mins/df["G"].astype(int)

    # Drop categorical and unnecessary columns
    columns_to_drop=["Pos", "Age", "Tm", "GS", "FG", "FG%", "3P", "3P%", "2P", "2PA", "2P%", "eFG%", "FT", "FT%", "TRB", "PTS"]
    df = df.drop(columns=columns_to_drop)

    # Convert data to numeric instead of object
    df = df.apply(pd.to_numeric)

#     # Divide columns by MP and multiply by MPG to get average stats per game
#     for col in df:
#         df[col] = df[col]/mins*mpg

#     # Add the minutes per game column to the dataframe
#     df["MPG"] = mpg
    
    return df

In [ ]:
def convertToPerGameStats(df):
    

In [7]:
# Get nba players data into dataframes from the year 2016 - present
currentYear = datetime.now().year
startYear = 2016
year_totals = {}

for year in range(startYear, currentYear+1):
    year_totals[year] = createPlayerDF('totals', str(year))

In [132]:
# Get nba team rosters into dataframes
nba_teams = teams.get_teams()
nba_team_abr = [team['abbreviation'] for team in nba_teams]
team_rosters = {}

# Convert abreviation for Brooklyn, Pheonix, & Charlotte for basketball-reference.com
nba_team_abr[14] = "BRK"
nba_team_abr[19] = "PHO"
nba_team_abr[29] = "CHO"

for team in nba_team_abr:
    team_rosters[team] = createRosters(team)

In [210]:
# Create dataframe for each player's per minute averages over the last 5 years
currentYear = datetime.now().year
player_totals = {}

for team in team_rosters:
    for player in team_rosters[team]:
        # Initializing
        player_totals[player] = [0,0,0,0,0,0,0,0,0,0,0,0]
        
        for i in range(0, 6):
            if player in player_totals[currentYear-i].index:
                player_totals[player] += createPlayerAverages(year_totals[currentYear-i]).loc[player]            

In [212]:
# Create a dataframe for each teams per minute average based on current roster
team_averages = {}

for team in team_rosters:
    # Initializing
    team_averages[team] = [0,0,0,0,0,0,0,0,0,0,0,0]
    
    for player in team_rosters[team]:
        team_averages[team] += player_averages[player]

In [215]:
player_totals[2020]

Pos Age   Tm   G  GS    MP   FG   FGA    FG%   3P  \
Player                                                                          
Steven Adams                  C  26  OKC  63  63  1680  283   478   .592    1   
Bam Adebayo                  PF  22  MIA  72  72  2417  440   790   .557    2   
LaMarcus Aldridge             C  34  SAS  53  53  1754  391   793   .493   61   
Kyle Alexander                C  23  MIA   2   0    13    1     2   .500    0   
Nickeil Alexander-Walker     SG  21  NOP  47   1   591   98   266   .368   46   
Grayson Allen                SG  24  MEM  38   0   718  117   251   .466   57   
Jarrett Allen                 C  21  BRK  70  64  1852  302   465   .649    0   
Kadeem Allen                 PG  27  NYK  10   0   117   19    44   .432    5   
Al-Farouq Aminu              PF  29  ORL  18   2   380   25    86   .291    9   
Justin Anderson              SG  26  BRK  10   1   107   10    38   .263    6   
Kyle Anderson                SF  26  MEM  67  28  1330  157   331   .474   24   
Ryan Anderson                 C  31  HOU   2   0    14    2     7   .286    1   
Giannis Antetokounmpo        PF  25  MIL  63  63  1917  685  1238   .553   89   
Kostas Antetokounmpo         PF  22  LAL   5   0    20    3     3  1.000    0   
Thanasis Antetokounmpo       SF  27  MIL  20   2   129   24    48   .500    0   
Carmelo Anthony              PF  35  POR  58  58  1902  336   782   .430   87   
OG Anunoby                   SF  22  TOR  69  68  2066  286   566   .505   89   
Ryan Arcidiacono             PG  25  CHI  58   4   930   90   220   .409   54   
Trevor Ariza                 SF  34  TOT  53  21  1493  142   324   .438   77   
D.J. Augustin                PG  32  ORL  57  13  1420  184   461   .399   70   
Deandre Ayton                 C  21  PHO  38  32  1236  310   568   .546    3   
Dwayne Bacon                 SG  24  CHO  39  11   687   85   244   .348   19   
Marvin Bagley III             C  20  SAC  13   6   334   78   167   .467    4   
Lonzo Ball                   PG  22  NOP  63  54  2025  277   687   .403  148   
Mo Bamba                      C  21  ORL  62   0   878  132   286   .462   37   
J.J. Barea                   PG  35  DAL  29   6   450   85   207   .411   32   
Harrison Barnes              PF  27  SAC  72  72  2482  365   793   .460  102   
RJ Barrett                   SG  19  NYK  56  55  1704  292   727   .402   63   
Will Barton                  SF  29  DEN  58  58  1916  332   738   .450  108   
Keita Bates-Diop          PF-SF  24  TOT  44   0   744  100   234   .427   34   
Nicolas Batum                SF  31  CHO  22   3   505   28    81   .346   14   
Aron Baynes                   C  33  PHO  42  28   934  183   381   .480   59   
Kent Bazemore                SF  30  TOT  68  21  1688  200   534   .375   84   
Darius Bazley                PF  19  OKC  61   9  1130  125   317   .394   49   
Bradley Beal                 SG  26  WAS  57  57  2053  593  1303   .455  170   
Malik Beasley                SG  23  TOT  55  14  1209  227   534   .425  107   
Marco Belinelli              SG  33  SAS  57   0   883  123   314   .392   67   
Jordan Bell                   C  25  TOT  29   0   256   35    67   .522    4   
DeAndre' Bembry              SG  25  ATL  43   4   915  104   228   .456   15   
Dragan Bender              PF-C  22  TOT  16   3   286   41    92   .446   15   
Dāvis Bertāns                PF  27  WAS  54   4  1583  265   610   .434  200   
Patrick Beverley             PG  31  LAC  51  50  1342  147   341   .431   80   
Khem Birch                    C  27  ORL  48  24   922   73   143   .510    0   
Goga Bitadze                  C  20  IND  54   2   471   70   150   .467    8   
Bismack Biyombo               C  27  CHO  53  29  1029  151   278   .543    0   
Nemanja Bjelica              PF  31  SAC  72  67  2011  314   653   .481  134   
Eric Bledsoe                 PG  30  MIL  61  61  1646  334   703   .475   74   
Bogdan Bogdanović            SG  27  SAC  61  28  1766  337

In [203]:
team_rosters["TOR"]

['Chris Boucher',
 'Fred VanVleet',
 'Svi Mykhailiuk',
 'Scottie Barnes',
 'Gary Trent Jr.',
 'Precious Achiuwa',
 'Dalano Banton',
 'Pascal Siakam',
 'OG Anunoby',
 'Malachi Flynn',
 'Justin Champagnie',
 'Khem Birch',
 'Yuta Watanabe',
 'Isaac Bonga',
 'Goran Dragić',
 'David Johnson']

In [213]:
player_totals["Precious Achiuwa"]

G        94
MP     1579
FGA     500
3PA      42
FTA     164
ORB     154
DRB     310
AST      72
STL      40
BLK      50
TOV      79
PF      167
Name: Precious Achiuwa, dtype: int64

In [200]:
team_averages["TOR"]

FGA     431.654051
3PA     169.532297
FTA     104.762231
ORB      52.629501
DRB     148.217007
AST     114.550021
STL      41.797467
BLK      23.080149
TOV      58.868088
PF       99.462307
MPG    1179.119931
Name: Chris Boucher, dtype: float64

In [202]:
team_averages["ATL"]

FGA     605.587168
3PA     217.993439
FTA     177.309522
ORB      72.296756
DRB     230.984193
AST     158.272178
STL      46.515357
BLK      32.909554
TOV      89.686558
PF      122.981939
MPG    1591.818104
Name: Trae Young, dtype: float64

In [137]:
test    

FGA    24.369313
3PA     8.400138
FTA     5.500112
ORB     3.445033
DRB    10.178161
AST     6.257533
STL     2.050025
BLK     1.741741
TOV     4.264333
PF      6.184418
Name: Jayson Tatum, dtype: float64

In [142]:
player_totals[2021]

Pos Age   Tm   G  GS    MP   FG   FGA    FG%   3P  \
Player                                                                          
Precious Achiuwa             PF  21  MIA  61   4   737  124   228   .544    0   
Jaylen Adams                 PG  24  MIL   7   0    18    1     8   .125    0   
Steven Adams                  C  27  NOP  58  58  1605  189   308   .614    0   
Bam Adebayo                   C  23  MIA  64  64  2143  456   800   .570    2   
LaMarcus Aldridge             C  35  TOT  26  23   674  140   296   .473   31   
Ty-Shon Alexander            SG  22  PHO  15   0    47    3    12   .250    2   
Nickeil Alexander-Walker     SG  22  NOP  46  13  1007  192   458   .419   76   
Grayson Allen                SG  25  MEM  50  38  1259  173   414   .418  107   
Jarrett Allen                 C  22  TOT  63  45  1864  298   482   .618    6   
Al-Farouq Aminu              PF  30  TOT  23  14   434   38    99   .384    8   
Kyle Anderson                PF  27  MEM  69  69  1887  308   658   .468   94   
Giannis Antetokounmpo        PF  26  MIL  61  61  2013  626  1100   .569   67   
Kostas Antetokounmpo         PF  23  LAL  15   0    56    3    10   .300    0   
Thanasis Antetokounmpo       SF  28  MIL  57   3   551   67   137   .489    7   
Carmelo Anthony              PF  36  POR  69   3  1690  327   777   .421  133   
Cole Anthony                 PG  20  ORL  47  34  1273  219   552   .397   58   
OG Anunoby                   SF  23  TOR  43  43  1433  249   519   .480  104   
Ryan Arcidiacono             PG  26  CHI  44   0   450   49   117   .419   25   
Trevor Ariza                 SF  35  MIA  30  27   841   99   241   .411   50   
D.J. Augustin                PG  33  TOT  57  12  1129  135   343   .394   83   
Deni Avdija                  SF  20  WAS  54  32  1257  130   312   .417   53   
Deandre Ayton                 C  22  PHO  69  69  2115  430   687   .626    4   
Udoka Azubuike                C  21  UTA  15   0    57    4     9   .444    0   
Dwayne Bacon                 SG  25  ORL  72  50  1853  292   726   .402   59   
Marvin Bagley III            PF  21  SAC  43  42  1112  247   490   .504   37   
LaMelo Ball                  PG  19  CHO  51  31  1469  293   672   .436   92   
Lonzo Ball                   PG  23  NOP  55  55  1747  290   700   .414  172   
Mo Bamba                      C  22  ORL  46   5   725  142   301   .472   38   
Desmond Bane                 SG  22  MEM  68  17  1519  234   499   .469  117   
Harrison Barnes              PF  28  SAC  58  58  2102  319   642   .497  100   
RJ Barrett                   SG  20  NYK  72  72  2511  467  1060   .441  124   
Will Barton                  SF  30  DEN  56  52  1736  259   608   .426   98   
Keita Bates-Diop             SF  25  SAS  30   0   245   30    67   .448    5   
Nicolas Batum                SF  32  LAC  67  38  1835  191   412   .464  110   
Aron Baynes                   C  34  TOR  53  31   980  134   304   .441   27   
Kent Bazemore                SF  31  GSW  67  18  1333  176   392   .449   75   
Darius Bazley                PF  20  OKC  55  55  1714  273   690   .396   83   
Bradley Beal                 SG  27  WAS  60  60  2147  670  1382   .485  130   
Malik Beasley                SG  24  MIN  37  36  1214  264   600   .440  128   
Jordan Bell                   C  26  TOT   6   1    82    7    22   .318    0   
DeAndre' Bembry              SF  26  TOR  51  12   972  117   228   .513   14   
Dāvis Bertāns                PF  28  WAS  57   7  1464  193   478   .404  169   
Patrick Beverley             PG  32  LAC  37  34   832   93   220   .423   56   
Saddiq Bey                   SF  21  DET  70  53  1909  279   691   .404  175   
Tyler Bey                    SF  22  DAL  18   0    71    7    22   .318    1   
Khem Birch                    C  28  TOT  67  22  1529  189   380   .497   13   
Goga Bitadze                  C  21  IND  45   3   561   83   194   .428   20   
Bismack Biyombo               C  28  CHO  66  36  1349  142

In [5]:
player_df = players_combined[2021]

In [9]:
month = "january"
year = "2021"

url = f'https://widgets.sports-reference.com/wg.fcgi?css=1&site=bbr&url=%2Fleagues%2FNBA_{year}_games-{month}.html&div=div_schedule'
html = requests.get(url).content
df_list = pd.read_html(html)
games_df = df_list[-1]

In [10]:
games_df.head()

Date Start (ET)    Visitor/Neutral  PTS       Home/Neutral  \
0  Fri, Jan 1, 2021      7:00p  Memphis Grizzlies  108  Charlotte Hornets   
1  Fri, Jan 1, 2021      7:00p         Miami Heat   83   Dallas Mavericks   
2  Fri, Jan 1, 2021      7:00p     Boston Celtics   93    Detroit Pistons   
3  Fri, Jan 1, 2021      7:30p      Atlanta Hawks  114      Brooklyn Nets   
4  Fri, Jan 1, 2021      8:00p      Chicago Bulls   96    Milwaukee Bucks   

   PTS.1 Unnamed: 6 Unnamed: 7  Attend.  Notes  
0     93  Box Score        NaN        0    NaN  
1     93  Box Score        NaN        0    NaN  
2     96  Box Score        NaN        0    NaN  
3     96  Box Score        NaN        0    NaN  
4    126  Box Score        NaN        0    NaN

In [31]:
roster_home = ["Devonte' Graham", "Terry Rozier", "Gordon Hayward", "P.J. Washington", "Bismack Biyombo", "Miles Bridges", "LaMelo Ball", "Cody Martin", "Caleb Martin", "Jalen McDaniels", "Malik Monk", "Nick Richards", "Vernon Carey Jr.", "Nate Darling"]
roster_away = ["Tyus Jones", "Dillon Brooks", "Kyle Anderson", "Brandon Clarke", "Jonas Valančiūnas", "Desmond Bane", "John Konchar", "Gorgui Dieng", "Sean McDermott"]

In [64]:
team_home = player_df.loc[roster_home]
team_away = player_df.loc[roster_away]

In [28]:
team_home

Pos Age   Tm   G  GS    MP   FG   FGA   FG%   3P  3PA   3P%  \
Player                                                                         
Devonte' Graham   PG  25  CHO  55  44  1659  252   669  .377  179  477  .375   
Terry Rozier      SG  26  CHO  69  69  2383  510  1134  .450  222  571  .389   
Gordon Hayward    SF  30  CHO  44  44  1496  311   658  .473   85  205  .415   
P.J. Washington   PF  22  CHO  64  61  1954  302   686  .440  112  290  .386   
Bismack Biyombo    C  28  CHO  66  36  1349  142   242  .587    0    1  .000   
Miles Bridges     PF  22  CHO  66  19  1932  313   622  .503  116  290  .400   
LaMelo Ball       PG  19  CHO  51  31  1469  293   672  .436   92  261  .352   
Cody Martin       SF  25  CHO  52  10   849   83   188  .441   16   58  .276   
Caleb Martin      SF  25  CHO  53   3   818   96   256  .375   31  125  .248   
Jalen McDaniels   SF  23  CHO  47  18   904  133   284  .468   35  105  .333   
Malik Monk        SG  22  CHO  42   0   878  173   399  .434   85  212  .401   
Nick Richards     PF  23  CHO  18   0    63    4     9  .444    0    1  .000   
Vernon Carey Jr.   C  19  CHO  19   4   115   18    36  .500    1    7  .143   
Nate Darling      SG  22  CHO   7   0    26    2     7  .286    2    7  .286   

                   2P  2PA   2P%  eFG%   FT  FTA    FT%  ORB  DRB  TRB  AST  \
Player                                                                        
Devonte' Graham    73  192  .380  .510  133  158   .842   22  126  148  295   
Terry Rozier      288  563  .512  .548  165  202   .817   47  255  302  293   
Gordon Hayward    226  453  .499  .537  156  185   .843   37  221  258  181   
P.J. Washington   190  396  .480  .522  108  145   .745   93  325  418  161   
Bismack Biyombo   142  241  .589  .587   47  105   .448  137  210  347   81   
Miles Bridges     197  332  .593  .596   98  113   .867   81  316  397  147   
LaMelo Ball       201  411  .489  .504  125  165   .758   63  239  302  313   
Cody Martin        67  130  .515  .484   25   43   .581   52  109  161   86   
Caleb Martin       65  131  .496  .436   41   64   .641   31  110  141   67   
Jalen McDaniels    98  179  .547  .530   45   64   .703   45  124  169   53   
Malik Monk         88  187  .471  .540   59   72   .819   14   87  101   87   
Nick Richards       4    8  .500  .444    7   11   .636    4    7   11    2   
Vernon Carey Jr.   17   29  .586  .514    9   11   .818    6   21   27    2   
Nate Darling        0    0        .429    3    3  1.000    1    0    1    1   

                 STL BLK  TOV   PF   PTS   PER   TS%   3PAr    FTr  ORB%  \
Player                                                                     
Devonte' Graham   48   6   84   77   816  14.6  .552   .713   .236   1.4   
Terry Rozier      87  26  128  119  1407  17.1  .575   .504   .178   2.1   
Gordon Hayward    52  14   91   74   863  17.6  .584   .312   .281   2.6   
P.J. Washington   69  79  128  171   824  13.4  .549   .423   .211   5.1   
Bismack Biyombo   17  74   71  141   331  11.7  .574   .004   .434  10.8   
Miles Bridges     44  52  106  143   840  14.7  .625   .466   .182   4.5   
LaMelo Ball       81  18  145  136   803  17.5  .539   .388   .246   4.6   
Cody Martin       37  12   40   52   207  10.6  .500   .309   .229   6.5   
Caleb Martin      37  12   33   62   264   9.5  .465   .488   .250   4.0   
Jalen McDaniels   28  19   45   95   346  11.4  .554   .370   .225   5.3   
Malik Monk        19   4   55   47   490  13.6  .569   .531   .180   1.7   
Nick Richards      0   0    3    7    15   5.5  .542   .111  1.222   6.8   
Vernon Carey Jr.   1   5    5   13    46  11.7  .563   .194   .306   5.6   
Nate Darling       0   1    1    1     9   8.2  .541  1.000   .429   4.1   

                  DRB%  TRB%  AST% STL% BLK%  TOV%  USG%     OWS  DWS   WS  \
Player                                                                       
Devonte' Graham    8.4   4.8  26.3  1.4  0.4  10.2  21.4     2.5  0.9  3.4   
Terry Rozier      11

In [34]:
team_away

Pos Age   Tm   G  GS    MP   FG   FGA   FG%   3P  3PA   3P%  \
Player                                                                          
Tyus Jones         PG  24  MEM  70   9  1222  178   413  .431   45  140  .321   
Dillon Brooks      SF  25  MEM  67  67  1997  432  1031  .419  128  372  .344   
Kyle Anderson      PF  27  MEM  69  69  1887  308   658  .468   94  261  .360   
Brandon Clarke     PF  24  MEM  59  16  1415  256   495  .517   20   77  .260   
Jonas Valančiūnas   C  28  MEM  62  61  1755  440   743  .592   21   57  .368   
Desmond Bane       SG  22  MEM  68  17  1519  234   499  .469  117  271  .432   
John Konchar       SG  24  MEM  43   0   575   69   138  .500   21   56  .375   
Gorgui Dieng        C  31  TOT  38   1   552   85   163  .521   30   70  .429   
Sean McDermott     SF  24  MEM  18   0   158   13    33  .394    5   22  .227   

                    2P  2PA   2P%  eFG%   FT  FTA    FT%  ORB  DRB  TRB  AST  \
Player                                                                         
Tyus Jones         133  273  .487  .485   41   45   .911   21  119  140  259   
Dillon Brooks      304  659  .461  .481  159  195   .815   53  143  196  157   
Kyle Anderson      214  397  .539  .540  144  184   .783   52  344  396  250   
Brandon Clarke     236  418  .565  .537   78  113   .690   97  231  328   95   
Jonas Valančiūnas  419  686  .611  .606  157  203   .773  253  523  776  112   
Desmond Bane       117  228  .513  .586   40   49   .816   31  179  210  118   
John Konchar        48   82  .585  .576   25   30   .833   35   93  128   47   
Gorgui Dieng        55   93  .591  .613   58   67   .866   40  100  140   48   
Sean McDermott       8   11  .727  .470    8    8  1.000    6   13   19    4   

                  STL BLK  TOV   PF   PTS   PER   TS%  3PAr   FTr  ORB%  DRB%  \
Player                                                                          
Tyus Jones         64   6   48   31   442  15.0  .511  .339  .109   1.8  10.4   
Dillon Brooks      78  26  119  237  1151  12.1  .515  .361  .189   2.8   7.7   
Kyle Anderson      84  57   86  120   854  17.2  .578  .397  .280   2.9  19.5   
Brandon Clarke     60  51   33   84   610  17.3  .560  .156  .228   7.2  17.5   
Jonas Valančiūnas  35  57  100  179  1058  24.4  .636  .077  .273  15.1  31.9   
Desmond Bane       41  16   59  125   625  12.2  .600  .543  .098   2.1  12.6   
John Konchar       30   9   18   40   184  14.8  .608  .406  .217   6.4  17.3   
Gorgui Dieng       26  16   32   56   258  19.2  .670  .429  .411   7.6  19.5   
Sean McDermott      2   3    4    8    39   7.2  .534  .667  .242   4.0   8.8   

                   TRB%  AST% STL% BLK%  TOV%  USG%     OWS  DWS   WS WS/48    \
Player                                                                          
Tyus Jones          6.1  28.6  2.5  0.4  10.0  16.6     1.5  1.3  2.8  .110     
Dillon Brooks       5.2  11.7  1.9  1.2   9.6  26.1    -0.5  1.8  1.4  .033     
Kyle Anderson      11.1  18.3  2.1  2.7  10.4  18.5     2.9  2.7  5.6  .143     
Brandon Clarke     12.3   9.5  2.0  3.2   5.7  17.2     2.2  2.0  4.2  .142     
Jonas Valančiūnas  23.4  10.0  1.0  2.9  10.7  22.4     5.1  2.6  7.8  .213     
Desmond Bane        7.3  10.6  1.3  0.9  10.2  16.1     1.6  1.3  2.9  .093     
John Konchar       11.8  10.7  2.5  1.4  10.6  12.4     0.9  0.8  1.7  .145     
Gorgui Dieng       13.5  12.0  2.3  2.6  14.3  17.4     1.3  0.8  2.1  .185     
Sean McDermott      6.4   3.1  0.6  1.7   9.9  10.8     0.1  0.1  0.2  .050     

                   OBPM  DBPM   BPM  VORP  
Player                                     
Tyus Jones         -0.1   0.9   0.8   0.9  
Dillon Brooks      -2.6  -1.1  -3.7  -0.9  
Kyle Anderson       1.4   1.9   3.3   2.5  
Brandon Clarke      0.4   1.2   1.5   1.3  
Jonas Valančiūnas   3.2  -0.3   3.0   2.2  
Desmond Bane       -0.6  -0.2  -0.8   0.5  
John Konchar       -0.2   1.4   1.2   0.5  
Gorgui Dieng        1.8   1.5   3.4   0.7  
Sean McDermott     -3

In [90]:
team_home_fin = team_home.reset_index(drop=True)

In [91]:
drop_columns = ["Pos", "Age", "Tm", "G", "GS", "FG%", "3P%", "2P", "2PA", "2P%", "eFG%", "FT%", "ORB", "DRB", "TS%", "3PAr", "FTr", "ORB%", "DRB%", "TRB%", "AST%", "STL%", "BLK%", "TOV%", "USG%", "WS/48", "OBPM", "DBPM", "BPM", "VORP"]
team_home_fin = team_home_fin.drop(columns=drop_columns)
team_home_fin = team_home_fin.dropna(axis=1, how="all")

In [92]:
team_home_fin = team_home_fin.drop(team_home_fin.columns[19], axis=1)

In [101]:
team_home_fin

FG       FGA        3P       3PA        FT       FTA       TRB  \
0   0.151899  0.403255  0.107896  0.287523  0.080169  0.095238  0.089210   
1   0.214016  0.475871  0.093160  0.239614  0.069240  0.084767  0.126731   
2   0.207888  0.439840  0.056818  0.137032  0.104278  0.123663  0.172460   
3   0.154555  0.351075  0.057318  0.148414  0.055271  0.074207  0.213920   
4   0.105263  0.179392  0.000000  0.000741  0.034841  0.077835  0.257228   
5   0.162008  0.321946  0.060041  0.150104  0.050725  0.058489  0.205487   
6   0.199455  0.457454  0.062628  0.177672  0.085092  0.112321  0.205582   
7   0.097762  0.221437  0.018846  0.068316  0.029446  0.050648  0.189635   
8   0.117359  0.312958  0.037897  0.152812  0.050122  0.078240  0.172372   
9   0.147124  0.314159  0.038717  0.116150  0.049779  0.070796  0.186947   
10  0.197039  0.454442  0.096811  0.241458  0.067198  0.082005  0.115034   
11  0.063492  0.142857  0.000000  0.015873  0.111111  0.174603  0.174603   
12  0.156522  0.313043  0.008696  0.060870  0.078261  0.095652  0.234783   
13  0.076923  0.269231  0.076923  0.269231  0.115385  0.115385  0.038462   

         AST       STL       BLK       TOV        PF       PTS       PER  \
0   0.177818  0.028933  0.003617  0.050633  0.046414  0.491863  0.008800   
1   0.122954  0.036509  0.010911  0.053714  0.049937  0.590432  0.007176   
2   0.120989  0.034759  0.009358  0.060829  0.049465  0.576872  0.011765   
3   0.082395  0.035312  0.040430  0.065507  0.087513  0.421699  0.006858   
4   0.060044  0.012602  0.054855  0.052632  0.104522  0.245367  0.008673   
5   0.076087  0.022774  0.026915  0.054865  0.074017  0.434783  0.007609   
6   0.213070  0.055140  0.012253  0.098707  0.092580  0.546630  0.011913   
7   0.101296  0.043581  0.014134  0.047114  0.061249  0.243816  0.012485   
8   0.081907  0.045232  0.014670  0.040342  0.075795  0.322738  0.011614   
9   0.058628  0.030973  0.021018  0.049779  0.105088  0.382743  0.012611   
10  0.099089  0.021640  0.004556  0.062642  0.053531  0.558087  0.015490   
11  0.031746  0.000000  0.000000  0.047619  0.111111  0.238095  0.087302   
12  0.017391  0.008696  0.043478  0.043478  0.113043  0.400000  0.101739   
13  0.038462  0.000000  0.038462  0.038462  0.038462  0.346154  0.315385   

         OWS       DWS        WS  
0   0.001507  0.000542  0.002049  
1   0.001385  0.000839  0.002182  
2   0.001471  0.000936  0.002340  
3   0.000154  0.001228  0.001382  
4   0.000667  0.001038  0.001705  
5   0.001242  0.000983  0.002174  
6   0.000681  0.001293  0.001906  
7   0.000236  0.001060  0.001296  
8  -0.000489  0.001100  0.000611  
9   0.000332  0.000996  0.001327  
10  0.000569  0.000569  0.001139  
11  0.000000  0.000000  0.000000  
12  0.000000  0.000870  0.001739  
13  0.000000  0.000000  0.000000

In [94]:
for col in team_home_fin:
    team_home_fin[col] = team_home_fin[col].astype(float)

In [98]:
for col in team_home_fin.columns[1:]:
    team_home_fin[col] = team_home_fin[col]/team_home_fin["MP"]
team_home_fin["PER"] = team_home_fin["PER"] * team_home_fin["MP"]

In [100]:
team_home_fin = team_home_fin.drop(columns="MP")

In [88]:
team_home_fin.dtypes

MP     float64
FG     float64
FGA    float64
3P     float64
3PA    float64
FT     float64
FTA    float64
TRB    float64
AST    float64
STL    float64
BLK    float64
TOV    float64
PF     float64
PTS    float64
PER    float64
OWS    float64
DWS    float64
WS     float64
dtype: object

In [102]:
team_home_fin = team_home_fin.sum()

In [104]:
team_home_fin

[FG     2.051305
 FGA    4.656960
 3P     0.715751
 3PA    2.065808
 FT     0.980918
 FTA    1.293849
 TRB    2.382452
 AST    1.281877
 STL    0.376151
 BLK    0.294657
 TOV    0.766322
 PF     1.062726
 PTS    5.799279
 PER    0.619418
 OWS    0.007754
 DWS    0.011455
 WS     0.019850
 dtype: float64]

In [105]:
!pip install nba_api

In [5]:
from nba_api.stats.static import teams

nba_teams = teams.get_teams()
# Select the dictionary for the Celtics, which contains their team ID
celtics = [team for team in nba_teams if team['abbreviation'] == 'BOS'][0]
celtics_id = celtics['id']

In [6]:
from nba_api.stats.endpoints import leaguegamefinder

# Query for games where the Celtics were playing
gamefinder = leaguegamefinder.LeagueGameFinder(team_id_nullable=celtics_id)
# The first DataFrame of those returned is what we want.
games = gamefinder.get_data_frames()[0]
games.head()

SEASON_ID     TEAM_ID TEAM_ABBREVIATION       TEAM_NAME     GAME_ID  \
0     22021  1610612738               BOS  Boston Celtics  0022100654   
1     22021  1610612738               BOS  Boston Celtics  0022100647   
2     22021  1610612738               BOS  Boston Celtics  0022100635   
3     22021  1610612738               BOS  Boston Celtics  0022100618   
4     22021  1610612738               BOS  Boston Celtics  0022100609   

    GAME_DATE      MATCHUP WL  MIN  PTS  FGM  FGA  FG_PCT  FG3M  FG3A  \
0  2022-01-17  BOS vs. NOP  W  241  104   38   80   0.475    10    32   
1  2022-01-15  BOS vs. CHI  W  240  114   44   90   0.489     9    26   
2  2022-01-14    BOS @ PHI  L  238   99   37   78   0.474    11    31   
3  2022-01-12    BOS @ IND  W  239  119   40   78   0.513    18    38   
4  2022-01-10  BOS vs. IND  W  265  101   35   88   0.398     8    28   

   FG3_PCT  FTM  FTA  FT_PCT  OREB  DREB  REB  AST  STL  BLK  TOV  PF  \
0    0.313   18   20   0.900     5    42   47   22    6    4   14  18   
1    0.346   17   19   0.895    17    33   50   27    6    6   11  15   
2    0.355   14   18   0.778     7    37   44   20    4    4   20  21   
3    0.474   21   25   0.840     7    30   37   23    6    5   11  22   
4    0.286   23   28   0.821    12    41   53   17   10    6   20  19   

   PLUS_MINUS  
0        12.0  
1         2.0  
2       -12.0  
3        19.0  
4         3.0

In [7]:
games

SEASON_ID     TEAM_ID TEAM_ABBREVIATION       TEAM_NAME     GAME_ID  \
0        22021  1610612738               BOS  Boston Celtics  0022100654   
1        22021  1610612738               BOS  Boston Celtics  0022100647   
2        22021  1610612738               BOS  Boston Celtics  0022100635   
3        22021  1610612738               BOS  Boston Celtics  0022100618   
4        22021  1610612738               BOS  Boston Celtics  0022100609   
5        22021  1610612738               BOS  Boston Celtics  0022100595   
6        22021  1610612738               BOS  Boston Celtics  0022100578   
7        22021  1610612738               BOS  Boston Celtics  0022100570   
8        22021  1610612738               BOS  Boston Celtics  0022100546   
9        22021  1610612738               BOS  Boston Celtics  0022100529   
10       22021  1610612738               BOS  Boston Celtics  0022100518   
11       22021  1610612738               BOS  Boston Celtics  0022100503   
12       22021  1610612738               BOS  Boston Celtics  0022100489   
13       22021  1610612738               BOS  Boston Celtics  0022100471   
14       22021  1610612738               BOS  Boston Celtics  0022100457   
15       22021  1610612738               BOS  Boston Celtics  0022100445   
16       22021  1610612738               BOS  Boston Celtics  0022100435   
17       22021  1610612738               BOS  Boston Celtics  0022100408   
18       22021  1610612738               BOS  Boston Celtics  0022100390   
19       22021  1610612738               BOS  Boston Celtics  0022100378   
20       22021  1610612738               BOS  Boston Celtics  0022100365   
21       22021  1610612738               BOS  Boston Celtics  0022100347   
22       22021  1610612738               BOS  Boston Celtics  0022100339   
23       22021  1610612738               BOS  Boston Celtics  0022100322   
24       22021  1610612738               BOS  Boston Celtics  0022100302   
25       22021  1610612738               BOS  Boston Celtics  0022100287   
26       22021  1610612738               BOS  Boston Celtics  0022100270   
27       22021  1610612738               BOS  Boston Celtics  0022100256   
28       22021  1610612738               BOS  Boston Celtics  0022100243   
29       22021  1610612738               BOS  Boston Celtics  0022100232   
30       22021  1610612738               BOS  Boston Celtics  0022100215   
31       22021  1610612738               BOS  Boston Celtics  0022100199   
32       22021  1610612738               BOS  Boston Celtics  0022100190   
33       22021  1610612738               BOS  Boston Celtics  0022100175   
34       22021  1610612738               BOS  Boston Celtics  0022100160   
35       22021  1610612738               BOS  Boston Celtics  0022100136   
36       22021  1610612738               BOS  Boston Celtics  0022100121   
37       22021  1610612738               BOS  Boston Celtics  0022100110   
38       22021  1610612738               BOS  Boston Celtics  0022100098   
39       22021  1610612738               BOS  Boston Celtics  0022100078   
40       22021  1610612738               BOS  Boston Celtics  0022100056   
41       22021  1610612738               BOS  Boston Celtics  0022100041   
42       22021  1610612738               BOS  Boston Celtics  0022100037   
43       22021  1610612738               BOS  Boston Celtics  0022100020   
44       22021  1610612738               BOS  Boston Celtics  0022100005   
45       12021  1610612738               BOS  Boston Celtics  0012100059   
46       12021  1610612738               BOS  Boston Celtics  0012100050   
47       12021  1610612738               BOS  Boston Celtics  0012100032   
48       12021  1610612738               BOS  Boston Celtics  0012100003   
49       22021  1610612738               BOS  Boston Celtics  1522100075   
50       22021  1610612738               BOS  Boston Celtics  1522100047   
51       22021  1610612738               BOS  Boston 

In [20]:
test = games.drop(columns=["SEASON_ID", "TEAM_ID", "TEAM_ABBREVIATION", "TEAM_NAME", "GAME_ID", "GAME_DATE", "MATCHUP", "WL", "MIN", "FG_PCT", "FG3_PCT", "FT_PCT", "REB", "PLUS_MINUS", "FGM", "FG3M", "FTM"])

In [21]:
test

PTS  FGA  FG3A  FTA  OREB  DREB  AST  STL  BLK  TOV  PF
0     104   80    32   20     5    42   22    6    4   14  18
1     114   90    26   19    17    33   27    6    6   11  15
2      99   78    31   18     7    37   20    4    4   20  21
3     119   78    38   25     7    30   23    6    5   11  22
4     101   88    28   28    12    41   17   10    6   20  19
5      99   76    29   17     9    36   26    8    8   10  15
6     105   80    45   13     8    30   22    5   10   12  16
7      97   90    28    9    13    28   19   10    9    8  12
8     116   86    36   28     9    37   25    5   10   21  23
9     123   83    27   26    13    38   28    6    7   17  18
10     82  101    42   11    21    29   19    8    8    8  16
11    103   89    47   28    15    38   23    8   10   14  16
12    113   89    45   24    11    33   24    9    8   14  23
13    111   92    30   18    12    36   24   12    5   13  24
14    103   82    27   25    11    31   16    9    5   18  23
15    114   89    45   17    12    33   23    6    3   12  20
16    107   82    41   29    11    34   20    5    2   16  19
17    117   86    47   13     7    33   31    6    5   11  15
18     90   93    26   24    15    31   13    7    6   13  17
19    111   86    32   21    14    33   26   11    3   22  21
20    102   82    33   29     7    27   27    8    4   13  16
21    145   87    37   29    12    34   26    5    7   11  21
22    130   91    39   22     5    25   23    9    3    6  22
23     88   79    28   15     4    42   18    5    8   13  15
24    109   82    34   31    12    41   24    5    3   17  19
25     88   92    34   15    12    39   20    4    8   10  20
26    104   91    48   28    15    30   25    6    5   11  24
27    108   92    35   19    11    47   19   10    3   14  24
28    111   88    39   14     8    40   28    4    7    7  11
29    130   88    30   38    12    39   22    7    2   12  20
30     99   84    41   17    12    30   24    9    2   14  17
31     98   78    29   20     6    40   23    7    6   14  16
32     89   78    23   18    10    37   20    7    3   19  16
33    122   96    41   18    16    37   22    5    7   16  12
34    104   94    29   15    12    32   21   10    5   15  13
35    104   86    31   16     8    28   20    6    2   11  14
36     95   78    41   20    11    35   16    7    4   16  16
37     92   79    37   25     9    41   24    7    9   11  20
38    114   96    33   20    13    25   20   10    1    9  15
39    112  107    26   25     8    46   23    8   10   11  32
40    107   85    29   28    10    27   18    9    5   13  21
41    140  101    50   25    11    42   33    8    9   12  23
42    107   86    47   20     6    37   22   10    6   11  22
43     83   82    34   11    10    32   19    6   12   25  19
44    134  117    57   23    15    41   34   13    9   18  24
45    100   81    41   20     5    31   20   12    4   18  22
46    102   91    39   14    10    35   23    8    5   12  17
47    113   81    40   21     8    41   29    5    8   23  20
48     98   91    40   23    13    38   19    9    6   16  14
49     67   59    36   17     5    34   19    2    8   28  17
50    100   81    27   17     9    38   22    8   12   13  24
51    108   75    44    9     7    35   33    8    5   13  20
52    107   79    32   20     9    36   25    7    1   12  25
53     85   81    51    9    11    28   22    6    1   11  22
54    109   92    40   23    13    31   18    3   12   11  21
55    126   84    40   42    11    23   24    8    4   10  21
56    125   89    39   23    13    33   21    5    3   13  25
57    108   92    34   23    15    28   23   10    4   15  20
58     93   84    30   26    11    29   19    6   12   12  18
59    118   96    45   32    14    35   20    8    5   10  17
60     92   86    41   15     9    37   19    4    6   12  19
61    124   95    42   18     9    35   27    8    6   14  24
62     94  101    41   14    13    33   14    9    8    7  23
63    121   88    37   17     3    29 

In [64]:
# Split our preprocessed data into our features and target arrays
X = test.drop("PTS", 1)
y = test["PTS"]

# Split the preprocessed data into a training and testing dataset
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42)

In [65]:
model = LinearRegression()
model.fit(X_train, y_train)
y_pred = model.predict(X_train)
y_pred

array([108.80455795,  87.02704202,  92.63993704, ...,  80.92581497,
       114.062698  , 117.60170176])

In [66]:
print(f'Training Score: {model.score(X_train, y_train)}')
print(f'Testing Score: {model.score(X_test, y_test)}')

Training Score: 0.6812653406570583
Testing Score: 0.7075634909190502


In [113]:
# Create a StandardScaler instances
scaler = StandardScaler()

# Fit the StandardScaler
X_scaler = scaler.fit(X_train)

# Scale the data
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

In [121]:
# Define the model - deep neural net
number_input_features = len(X_train_scaled[0])
hidden_nodes_layer1 = 40
hidden_nodes_layer2 = 10

nn = tf.keras.models.Sequential()

# First hidden layer
nn.add(tf.keras.layers.Dense(units=hidden_nodes_layer1, input_dim=number_input_features, activation="relu"))

# Second hidden layer
nn.add(tf.keras.layers.Dense(units=hidden_nodes_layer2, activation="relu"))

# Output layer
nn.add(tf.keras.layers.Dense(units=1, activation="relu"))

# Check the structure of the model
nn.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_3 (Dense)             (None, 40)                560       
                                                                 
 dense_4 (Dense)             (None, 10)                410       
                                                                 
 dense_5 (Dense)             (None, 1)                 11        
                                                                 
Total params: 981
Trainable params: 981
Non-trainable params: 0
_________________________________________________________________


In [122]:
# Compile the model
nn.compile(loss="mean_squared_error", optimizer="adam", metrics=["accuracy"])

In [123]:
# Train the model
fit_model = nn.fit(X_train_scaled, y_train, epochs=100, validation_data=(X_test_scaled, y_test))

Epoch 1/100
86/86 [==============================] - 1s 2ms/step - loss: 10391.9424 - accuracy: 0.0000e+00 - val_loss: 9745.6641 - val_accuracy: 0.0000e+00
Epoch 2/100
86/86 [==============================] - 0s 2ms/step - loss: 8558.0137 - accuracy: 0.0000e+00 - val_loss: 6877.9507 - val_accuracy: 0.0000e+00
Epoch 3/100
86/86 [==============================] - 0s 1ms/step - loss: 4816.2993 - accuracy: 0.0000e+00 - val_loss: 2648.8538 - val_accuracy: 0.0000e+00
Epoch 4/100
86/86 [==============================] - 0s 1ms/step - loss: 1515.6088 - accuracy: 0.0000e+00 - val_loss: 752.3105 - val_accuracy: 0.0000e+00
Epoch 5/100
86/86 [==============================] - 0s 1ms/step - loss: 675.1307 - accuracy: 0.0000e+00 - val_loss: 519.3492 - val_accuracy: 0.0000e+00
Epoch 6/100
86/86 [==============================] - 0s 1ms/step - loss: 544.2515 - accuracy: 0.0000e+00 - val_loss: 435.8842 - val_accuracy: 0.0000e+00
Epoch 7/100
86/86 [==============================] - 0s 1ms/step - loss: 4

Epoch 55/100
86/86 [==============================] - 0s 1ms/step - loss: 1.8634 - accuracy: 0.0000e+00 - val_loss: 1.8593 - val_accuracy: 0.0000e+00
Epoch 56/100
86/86 [==============================] - 0s 1ms/step - loss: 1.6895 - accuracy: 0.0000e+00 - val_loss: 1.8119 - val_accuracy: 0.0000e+00
Epoch 57/100
86/86 [==============================] - 0s 1ms/step - loss: 1.5572 - accuracy: 0.0000e+00 - val_loss: 1.6033 - val_accuracy: 0.0000e+00
Epoch 58/100
86/86 [==============================] - 0s 1ms/step - loss: 1.4349 - accuracy: 0.0000e+00 - val_loss: 1.5323 - val_accuracy: 0.0000e+00
Epoch 59/100
86/86 [==============================] - 0s 1ms/step - loss: 1.3324 - accuracy: 0.0000e+00 - val_loss: 1.3636 - val_accuracy: 0.0000e+00
Epoch 60/100
86/86 [==============================] - 0s 1ms/step - loss: 1.1929 - accuracy: 0.0000e+00 - val_loss: 1.3119 - val_accuracy: 0.0000e+00
Epoch 61/100
86/86 [==============================] - 0s 1ms/step - loss: 1.0758 - accuracy: 0.0000e

In [124]:
# Evaluate the model using the test data
model_loss, model_accuracy = nn.evaluate(X_test_scaled,y_test,verbose=2)
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")

29/29 - 0s - loss: 0.0867 - accuracy: 0.0000e+00 - 38ms/epoch - 1ms/step
Loss: 0.08666856586933136, Accuracy: 0.0


In [26]:
model = LinearRegression()

In [27]:
model.fit(X, y)

LinearRegression()

In [28]:
y_pred = model.predict(X)

In [29]:
y_pred

array([100.04876065, 105.66373762,  94.37855633, ..., 109.70337735,
       107.90901682, 116.88866167])

In [133]:
y

array([104, 114,  99, ..., 119, 108, 121], dtype=int64)

In [135]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42)

In [136]:
# Resample the training data with the BalancedRandomForestClassifier
from imblearn.ensemble import BalancedRandomForestClassifier

clf = BalancedRandomForestClassifier(random_state=1, n_estimators=100).fit(X_train, y_train)

In [141]:
from sklearn.metrics import balanced_accuracy_score
from sklearn.metrics import confusion_matrix
from imblearn.metrics import classification_report_imbalanced

In [139]:
# Calculated the balanced accuracy score
y_pred = clf.predict(X_test)
balanced_accuracy_score(y_test, y_pred)

D:\Anaconda\envs\PythonData\lib\site-packages\sklearn\metrics\_classification.py:1850: UserWarning: y_pred contains classes not in y_true
  warnings.warn('y_pred contains classes not in y_true')


0.026220816549474803

In [142]:
# Display the confusion matrix
confusion_matrix(y_test, y_pred)

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [1, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=int64)

In [143]:
model.fit(X_train, y_train)
training_score = model.score(X_train, y_train)
testing_score = model.score(X_test, y_test)

In [144]:
print(f"Training Score: {training_score}")
print(f"Testing Score: {testing_score}")

Training Score: 1.0
Testing Score: 1.0
